In [5]:
!pip install --upgrade langchain openai  -q

In [6]:
!pip install sentence_transformers -q

In [7]:
!apt-get install poppler-utils 

Reading package lists... Done
Building dependency tree       
Reading state information... Done
poppler-utils is already the newest version (0.86.1-0ubuntu1.1).
0 upgraded, 0 newly installed, 0 to remove and 28 not upgraded.


In [8]:
!pip install unstructured -q
!pip install unstructured[local-inference] -q
!pip install detectron2@git+https://github.com/facebookresearch/detectron2.git@v0.6#egg=detectron2 -q

  Preparing metadata (setup.py) ... done


In [9]:
pwd

'/content'

In [10]:
ls

'ML Model Database'/   sample_data/   tt/   tttttt/


In [11]:
ls

'ML Model Database'/   sample_data/   tt/   tttttt/


In [12]:
import time
from langchain.document_loaders import DirectoryLoader

directory = '/content/ML Model Database'

def load_docs(directory):
  loader = DirectoryLoader(directory)
  documents = loader.load()
  return documents

start_time = time.time()
documents = load_docs(directory)
end_time = time.time()

execution_time = end_time - start_time
print("Execution time: {:.2f} seconds".format(execution_time))


Execution time: 979.27 seconds


In [13]:
documents

[Document(page_content='SHIFTING HOUSEHOLD ENERGY USE IN BANGALORE, INDIA: USING BEHAVIORALLY INFORMED ENERGY REPORTS\n\nMINDY HERNANDEZ, KIRAN BHAGAVATULA, SANTHOSH CIBI, RAVICHANDRAN K, SUMATHY KRISHNAN, SUMEDHA MALAVIYA, AND BHARATH JAIRAJ\n\nEXECUTIVE SUMMARY Highlights ▪ From an equity and economic development\n\nperspective, it is critical for more Indian households to become electrified. However, because of the Indian grid’s dependence on fossil fuels, household electricity use in India is a major contributor to rising greenhouse gas (GHG) emissions and other externalities, like air pollution.\n\n▪ Evidence from social science research, largely\n\nfrom the United States, indicates that behaviorally designed household energy reports (HERs) that feature energy savings recommendations and social norm comparisons can decrease inefficient, excess consumption and environmental impacts.\n\n▪ This working paper details the results of a study\n\nof over 2,000 households in Bangalore, Ind

In [15]:
from langchain.text_splitter import RecursiveCharacterTextSplitter

def split_docs(documents,chunk_size=4000,chunk_overlap=20):
  text_splitter = RecursiveCharacterTextSplitter(chunk_size=chunk_size, chunk_overlap=chunk_overlap)
  docs = text_splitter.split_documents(documents)
  return docs

start_time = time.time()
docs = split_docs(documents)
end_time = time.time()
execution_time = end_time - start_time
print("Execution time: {:.2f} seconds".format(execution_time))

print(len(docs))

Execution time: 0.16 seconds
1997


In [16]:
print(docs[100])


page_content='visits using a pictorial handbook increased IFA compliance and haemoglobin levels\n\n(Nahrisah et al.,2020\x00.\n\nForgetfulness could be addressed by innovative program design elements, including\n\ndirect observation of pill intake. A randomised controlled trial of 400 pregnant\n\nwomen in rural North India found that direct monitoring of pill uptake by ASHAs\n\ndrives consumption, even when only the ﬁrst dose was monitored (Ahamed et al.\n\n2019\x00. Further, a (non-randomised) controlled trial of 140 pregnant women in\n\nBelgaum, India, ﬁnds positive e\ue007ects from direct observation from neighbours /\n\nother women from the same village as volunteer observers (Bilimale et al., 2010\x00.\n\nSuch interventions would require careful consideration of their scalability and\n\nfeasibility to avoid potential challenges to women’s autonomy.\n\nReminders are another intervention aimed at reducing forgetfulness and building an\n\nIFA daily habit. Home-based reminders could b

In [17]:
from langchain.embeddings import SentenceTransformerEmbeddings
embeddings = SentenceTransformerEmbeddings(model_name="all-MiniLM-L6-v2")

In [18]:
query_result = embeddings.embed_query("Hello world")
len(query_result)

384

In [19]:
!pip install pinecone-client -q


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 177.2/177.2 kB 4.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.0/60.0 kB 5.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 283.7/283.7 kB 14.3 MB/s eta 0:00:00


In [20]:
import pinecone 
from langchain.vectorstores import Pinecone
# initialize pinecone
pinecone.init(
    api_key="48a54b8a-23b8-41cd-ab93-b51f28044663",  # find at app.pinecone.io
    environment="us-east-1-aws"  # next to api key in console
)

index_name = "open-source"

start_time = time.time()
index = Pinecone.from_documents(docs, embeddings, index_name=index_name)
end_time = time.time()
time_taken = end_time - start_time

print("Time taken to index: {:.2f} seconds".format(time_taken))

Time taken to index: 474.69 seconds


In [21]:
def get_similiar_docs(query,k=1,score=False):
  if score:
    similar_docs = index.similarity_search_with_score(query,k=k)
  else:
    similar_docs = index.similarity_search(query,k=k)
  return similar_docs

query = "What is Washing with hope?"
similar_docs = get_similiar_docs(query)
similar_docs


[Document(page_content='Conclusions Overall, results indicate that HOPE SOAP© does, in- deed, give cause for hope. There is evidence that it may improve, and induce sustained handwashing behaviour among young children and, if used correctly, improve health outcomes. If HOPE SOAP© can be produced and sold at the same price as regular soap it could well prove to be a more effective intervention than simple soap dis- tribution. The results of our pilot study indicate that fur- ther research on this novel handwashing', metadata={'source': '/content/data/Washing with hope.pdf'})]